In [ ]:
import pandas as pd
import numpy as np
import itertools
import datetime
import exploration.dispersion as disp
import matplotlib.pyplot as plt
import statsmodels.formula.api as smf
import analytics.tranche_data as tdata
import ipysheet

from analytics.basket_index import MarkitBasketIndex
from analytics import on_the_run
from statsmodels.graphics.regressionplots import plot_fit
from scipy.special import logit, expit
from pygam import LinearGAM, s, f, GAM
from utils.db import dbengine, dbconn

In [ ]:
%matplotlib inline

In [ ]:
value_date = (datetime.datetime.today() - pd.offsets.BDay(1)).date()
start = (datetime.datetime.today() - pd.offsets.BDay(1) * 365 *4).date()
#end = (start + pd.offsets.BDay(1) * 365).date()
end = datetime.datetime.today()
gini_model, gini_results = {}, {}
conn = dbconn("serenitasdb")
conn.autocommit = True
for index_type in ['HY', 'IG', 'EU', 'XO']:
    risk = disp.get_tranche_data(dbconn("serenitasdb"), index_type)
    risk = risk[risk.index_duration > 1] #filter out the short duration ones
    gini_results[index_type], gini_model[index_type] = disp.create_models_v2(conn, risk)
    #fitted = gini_model[index_type].fit()
    #w = 1/(expit(fitted.fittedvalues + fitted.resid) -expit(fitted.fittedvalues))**2
    #gini_results[index_type], gini_model[index_type] = disp.create_models_v2(conn, risk, w)
gini_model['HY'].fit().summary()

fieldlist = ['exp_percentage','dispersion','gini','tranche_loss_per','mispricing']
for index_type in ['HY', 'IG', 'EU', 'XO']:
    gini_results[index_type][fieldlist].to_csv('/home/serenitas/edwin/' + index_type + '_results.csv')

In [ ]:
fieldlist = ['exp_percentage','dispersion','gini','tranche_loss_per','mispricing']
for index_type in ['HY', 'IG', 'EU', 'XO']:
    gini_results[index_type][fieldlist].to_csv('/home/serenitas/edwin/' + index_type + '_results.csv')

In [ ]:
#plot the residuals
fitted = gini_model['HY'].fit()
plt.figure(figsize=(8,5))
p=plt.scatter(x=expit(fitted.fittedvalues),y=expit(fitted.fittedvalues + fitted.resid) -expit(fitted.fittedvalues),edgecolor='k')
xmin=min(expit(fitted.fittedvalues))
xmax = max(expit(fitted.fittedvalues))
plt.hlines(y=0,xmin=xmin*0.9,xmax=xmax*1.1,color='red',linestyle='--',lw=3)
plt.xlabel("Fitted values",fontsize=15)
plt.ylabel("Residuals",fontsize=15)
plt.title("Fitted vs. residuals plot",fontsize=18)
plt.grid(True)
plt.show()

In [ ]:
#plot the gini coefficients
ginis = gini_results['HY'].xs([0, '5yr', 'HY'],level=['attach','tenor', 'index']).groupby(['date', 'series']).nth(-1).gini.unstack(level='series')
ginis.plot()

In [ ]:
#sheet = ipysheet.sheet(rows=2000, columns=7, column_headers=False, row_headers=False)
import IPython
pd.set_option("display.max_rows", None)
#IPython.OutputArea.auto_scroll_threshold = 20
ginis.sort_index(ascending=False)

In [ ]:
#look at Volatility vs Correlation

In [ ]:
#use RFE to get the model instead
from sklearn.preprocessing import PolynomialFeatures, PowerTransformer, normalize
from sklearn.linear_model import LinearRegression
from sklearn.pipeline import make_pipeline
from sklearn.feature_selection import RFECV, SelectKBest, f_regression
from sklearn.compose import TransformedTargetRegressor

import numpy as np

class MyTransformedTargetRegressor(TransformedTargetRegressor):
    @property
    def coef_(self):
        return self.regressor_.coef_
    
    @property
    def feature_importances_(self):
        return self.regressor_.feature_importances_
    
index_type = 'HY'

In [ ]:
all_variable_list = ['tranche_loss_per', 'tranche_id', 'index_price', 'index_basis', 'detach', 'corr_at_detach', 
                     'attach_adj', 'detach_adj', 'index_theta', 'delta','gamma', 'corr01', 'expected_loss', 
                     'exp_percentage', 'indexfactor', 'duration', 'index_expected_loss',
                     #Comment out to include
    #                'index_duration',
                     'theta',
                     'cumulativeloss',
    #                'att_moneyness',
                    'det_moneyness',
                     'thickness',
    #                'moneyness',
    #                'dispersion',
                     'gini',
                     'forward_delta']

def run_rfe(index_type):
    risk = disp.get_tranche_data(dbconn("serenitasdb"), index_type)
    attach_max = risk.index.get_level_values("attach").max()
    bottom_stack = risk[risk.index.get_level_values("attach") != attach_max]
    bottom_stack = bottom_stack[bottom_stack.tranche_loss_per > 0].dropna()

    #prepare the variables
    y = bottom_stack['tranche_loss_per']
    X = bottom_stack.drop(all_variable_list, axis=1)

    poly = PolynomialFeatures(3)
    X = pd.DataFrame(PowerTransformer().fit_transform(X), index=X.index, columns=X.columns)
    X_p = pd.DataFrame(poly.fit_transform(X), columns= poly.get_feature_names(X.columns))
    regr = MyTransformedTargetRegressor(regressor=LinearRegression(), func=logit, inverse_func=expit)

    rfecv = RFECV(regr).fit(X_p,y)

    df = pd.merge(risk, 
                       pd.DataFrame(rfecv.predict(X_p), 
                                    index=X.index, 
                                    columns=['predict_tranche_loss']),
                      how='left', left_index=True, right_index=True)

    df.loc[df.index.get_level_values("attach") != attach_max, "predict_tranche_loss_per_index"] = (
        df.predict_tranche_loss * df.thickness / df.index_expected_loss
    )

    def aux(s):
        temp = s.values
        temp[-1] = 1 - temp[:-1].sum()
        return temp

    df["predict_tranche_loss_per_index"] = df.groupby(["index", "series", "date"])["predict_tranche_loss_per_index"].transform(aux)
    df = df.assign(
        mispricing=(df.exp_percentage - df.predict_tranche_loss_per_index)
        * df.index_expected_loss
        / (df.detach_adj - df.attach_adj)
    )

    print(index_type, " Chosen columns: ", X_p[X_p.columns[rfecv.support_]].columns)
    print(index_type, " Score: ",  rfecv.score(X_p, y))
    
    return rfecv, df

gini_model, gini_results = {}, {}
for index_type in ['HY', 'IG', 'EU', 'XO']:
    gini_model[index_type], gini_results[index_type] = run_rfe(index_type)
fieldlist = ['exp_percentage','dispersion','gini','tranche_loss_per','mispricing']
for index_type in ['HY', 'IG', 'EU', 'XO']:
    gini_results[index_type][fieldlist].to_csv('/home/serenitas/edwin/' + index_type + '_results_rfecv.csv')

In [ ]:
gini_model, gini_results = {}, {}
for index_type in ['HY', 'IG', 'EU', 'XO']:
    gini_model[index_type], gini_results[index_type] = run_rfe(index_type)
fieldlist = ['exp_percentage','dispersion','gini','tranche_loss_per','mispricing']
for index_type in ['HY', 'IG', 'EU', 'XO']:
    gini_results[index_type][fieldlist].to_csv('/home/serenitas/edwin/' + index_type + '_results_rfecv.csv')

In [ ]:
# Plot number of features VS. cross-validation scores
index_type = 'IG'
plt.figure()
plt.xlabel("Number of features selected")
plt.ylabel("Cross validation score (nb of correct classifications)")
plt.plot(range(1, len(gini_model[index_type].grid_scores_) + 1), gini_model[index_type].grid_scores_)
plt.show()